In [1]:
outdir <- "/data2/mito_lineage/Analysis/annotation/output/data"
prefix <- "CHIP_april08_2021_Croker/MTblacklist/"
singlecell_sumstats_dir <- "/data2/isshamie/mito_lineage/data/processed/mtscATAC/CHIP_april08_2021_Croker/MTblacklist/"
cellr_indir <- "/data2/isshamie/mito_lineage/data/processed/mtscATAC/CHIP_april08_2021_Croker/MTblacklist"
external_dat_dir <- "/data2/mito_lineage/Analysis/annotation/output/data/granja_cd34"
external_frag_file <- "granja_cd34.fragments.tsv"
external_prefix <- "GSE129785_scATAC-Hematopoiesis-CD34"
exp <- "Flt3l"

In [2]:
library(EnsDb.Hsapiens.v75)

library(Signac)
library(Seurat)
library(data.table)
library(dplyr)
library(umap)
library(SummarizedExperiment)

Loading required package: ensembldb

Loading required package: BiocGenerics

Loading required package: parallel


Attaching package: ‘BiocGenerics’


The following objects are masked from ‘package:parallel’:

    clusterApply, clusterApplyLB, clusterCall, clusterEvalQ,
    clusterExport, clusterMap, parApply, parCapply, parLapply,
    parLapplyLB, parRapply, parSapply, parSapplyLB


The following objects are masked from ‘package:stats’:

    IQR, mad, sd, var, xtabs


The following objects are masked from ‘package:base’:

    anyDuplicated, append, as.data.frame, basename, cbind, colnames,
    dirname, do.call, duplicated, eval, evalq, Filter, Find, get, grep,
    grepl, intersect, is.unsorted, lapply, Map, mapply, match, mget,
    order, paste, pmax, pmax.int, pmin, pmin.int, Position, rank,
    rbind, Reduce, rownames, sapply, setdiff, sort, table, tapply,
    union, unique, unsplit, which.max, which.min


Loading required package: GenomicRanges

Loading required package: stats4

Loa

In [3]:
genome_dir <- outdir
outdir <- file.path(outdir, prefix)
#dir.create(outdir, recursive=TRUE, showWarnings = TRUE)

In [4]:
if (FALSE){
    BiocManager::install("EnsDb.Hsapiens.v75")
    }

In [5]:
if(FALSE){
  library(GenomeInfoDb)
  library(EnsDb.Hsapiens.v75)
  
  # extract gene coordinates from Ensembl, and ensure name formatting is consistent with Seurat object 
  gene.coords <- genes(EnsDb.Hsapiens.v75, filter = ~ gene_biotype == "protein_coding")
  seqlevelsStyle(gene.coords) <- 'UCSC'
  genebody.coords <- keepStandardChromosomes(gene.coords, pruning.mode = 'coarse')
  genebodyandpromoter.coords <- Extend(x = gene.coords, upstream = 2000, downstream = 0)
  saveRDS(genebodyandpromoter.coords, file.path(genome_dir, "genebodyandpromoter.coords_EnsDb.Hsapiens.v75.rds"))
}else{
genebodyandpromoter.coords <- readRDS(file.path(genome_dir, "genebodyandpromoter.coords_EnsDb.Hsapiens.v75.rds"))
}

In [6]:
genebodyandpromoter.coords

GRanges object with 22810 ranges and 6 metadata columns:
          seqnames            ranges strand |         gene_id   gene_name
             <Rle>         <IRanges>  <Rle> |     <character> <character>
      [1]     chr1       67091-70008      + | ENSG00000186092       OR4F5
      [2]     chr1     134901-141379      - | ENSG00000237683  AL627309.1
      [3]     chr1     365640-368634      + | ENSG00000235249      OR4F29
      [4]     chr1     621059-624053      - | ENSG00000185097      OR4F16
      [5]     chr1     738532-741137      - | ENSG00000269831  AL669831.1
      ...      ...               ...    ... .             ...         ...
  [22806]     chrY 26909216-26961626      - | ENSG00000187191        DAZ3
  [22807]     chrY 26978008-27053183      + | ENSG00000205916        DAZ4
  [22808]     chrY 27177048-27210695      - | ENSG00000185894       BPY2C
  [22809]     chrY 27766264-27771049      + | ENSG00000172288        CDY1
  [22810]     chrY 28111776-28116889      - | ENSG00000

In [7]:
unique(seqnames(genebodyandpromoter.coords))

[1] chr1               chr10              chr11             
  [4] chr12              chr13              chr14             
  [7] chr15              chr16              chr17             
 [10] chr18              chr19              chr2              
 [13] chr20              chr21              chr22             
 [16] chr3               chr4               chr5              
 [19] chr6               chr7               chr8              
 [22] chr9               GL000191.1         GL000192.1        
 [25] GL000193.1         GL000194.1         GL000195.1        
 [28] GL000201.1         GL000204.1         GL000205.1        
 [31] GL000209.1         GL000212.1         GL000213.1        
 [34] GL000215.1         GL000218.1         GL000219.1        
 [37] GL000221.1         GL000222.1         GL000223.1        
 [40] GL000228.1         GL000237.1         GL000242.1        
 [43] chr4_gl877872_fix  chr8_gl383535_fix  chr5_jh159133_fix 
 [46] chr10_kb663606_fix chr19_kb021647_fix chr5_ke332497_fix 
 [49] chr3_jh159131_fix  chr12_gl949745_alt chr17_jh720447_fix
 [52] chr7_gl582968_fix  chr16_jh720446_fix chr10_jh591181_fix
 [55] chr11_jh720443_fix chr7_jh159134_fix  chr1_jh636052_fix 
 [58] chr1_jh636053_fix  chr1_jh636054_fix  chr6_jh636056_fix 
 [61] chr7_jh636058_fix  chr6_jh636057_fix  chr19_ke332505_fix
 [64] chrX_jh720451_fix  chrX_jh720452_fix  chrX_jh720453_fix 
 [67] chrX_jh720454_fix  chr11_jh159136_alt chrX_jh806587_fix 
 [70] chrX_jh806590_fix  chrX_jh806591_fix  chrX_jh806592_fix 
 [73] chrX_jh806593_fix  chrX_jh806594_fix  chrX_jh806595_fix 
 [76] chrX_jh806596_fix  chrX_jh806597_fix  chr20_jh720448_fix
 [79] chrX_jh806598_fix  chrX_jh806599_fix  chrX_jh806600_fix 
 [82] chrX_jh806601_fix  chrX_jh806602_fix  chr10_jh806580_fix
 [85] chr22_jh806583_fix chrX_jh159150_fix  chr7_gl582969_fix 
 [88] chr9_jh806578_fix  chr9_jh806579_fix  chr11_jh159137_alt
 [91] chr14_kb021645_fix chr12_kb663607_fix chr8_ke332500_fix 
 [94] chr4_ke332496_fix  chr17_gl383558_fix chr17_gl582976_fix
 [97] chr3_gl383523_fix  chr6_ke332498_fix  chr8_gl949743_fix 
[100] chr21_ke332506_fix chr8_gl383536_fix  chr11_jh591184_fix
[103] chr17_jh636061_fix chr6_jh806576_fix  chr3_gl383524_fix 
[106] chr11_gl582973_fix chr11_jh159138_fix chrX_kb021648_fix 
[109] chr11_jh159139_fix chr11_jh159140_fix chr10_jh591182_fix
[112] chr3_jh159132_fix  chr22_jh720449_fix chr10_jh591183_fix
[115] chr12_jh720444_fix chr11_jh159141_fix chr6_kb663604_fix 
[118] chrX_jh720455_fix  chr17_kb021646_fix chr11_jh159142_fix
[121] chr11_jh159143_fix chr17_jh806582_fix chr8_jh159135_fix 
[124] chr7_ke332499_fix  chr22_jh806586_fix chr20_gl582979_fix
[127] chr13_gl582975_fix chr11_gl949744_fix chr10_gl383543_fix
[130] chr2_gl877871_fix  chr4_gl582967_fix  chr19_jh159149_fix
[133] chr19_gl582977_fix chr7_gl582970_fix  chr17_gl383559_fix
[136] chr17_jh159144_fix chr17_jh591186_fix chr17_gl383560_fix
[139] chr9_gl339450_fix  chr7_gl582971_fix  chr12_gl582974_fix
[142] chr11_jh806581_fix chr10_jh636060_fix chr11_jh591185_fix
[145] chr17_jh159145_fix chr10_gl877873_fix chr7_gl582972_fix 
[148] chr2_kb663603_fix  chr3_ke332495_fix  chr9_jh636059_fix 
[151] chr15_jh720445_fix chr10_ke332501_fix chr17_gl383561_fix
[154] chr1_gl949741_fix  chr17_gl383562_fix chr3_gl383525_fix 
[157] chr12_gl383548_fix chr9_gl383537_fix  chr9_gl383538_fix 
[160] chr1_gl383516_fix  chr10_gl383545_alt chr10_gl383546_alt
[163] chr12_gl877875_alt chr12_gl383550_alt chr12_gl877876_alt
[166] chr12_gl383553_alt chr15_gl383554_alt chr15_gl383555_alt
[169] chr16_gl383556_alt chr16_gl383557_alt HSCHR17_1         
[172] chr17_gl383563_alt chr17_gl383564_alt chr17_gl383566_alt
[175] chr17_jh159146_alt chr17_jh159147_alt chr17_jh159148_alt
[178] chr18_gl383567_alt chr18_gl383571_alt chr18_gl383572_alt
[181] chr19_gl949746_alt chr19_gl949747_alt chr19_gl949748_alt
[184] chr19_gl949749_alt chr19_gl949750_alt chr19_gl949751_alt
[187] chr19_gl949752_alt chr19_gl949753_alt chr19_gl383573_alt
[190] chr19_gl383574_alt chr19_gl

In [8]:
qcdf <- fread(file.path(singlecell_sumstats_dir, exp, "outs", "filtered_peak_bc_matrix", "barcodes.tsv"), header = FALSE, sep = ",", col.names=c('cell_id')) %>% 
      data.frame() %>% filter(cell_id != "None")
cells <- as.character(qcdf$cell_id)
cells

[1] "AAACGAAAGGAAACTT-1" "AAACGAAGTCCAAGAG-1" "AAACGAAGTCCGAGCT-1"
   [4] "AAACGAAGTTCAGAAA-1" "AAACGAAGTTTGAAGA-1" "AAACGAATCAGCCGGT-1"
   [7] "AAACGAATCCCAGTAA-1" "AAACGAATCCGGGCAT-1" "AAACGAATCCTGAAAC-1"
  [10] "AAACGAATCGATGTGT-1" "AAACGAATCGCCAGAC-1" "AAACGAATCGTGAACT-1"
  [13] "AAACTCGAGGAATGGA-1" "AAACTCGAGGTACACG-1" "AAACTCGCAAGACACG-1"
  [16] "AAACTCGCAATCCATG-1" "AAACTCGCACTAGGAG-1" "AAACTCGCACTGAAGG-1"
  [19] "AAACTCGCACTGTTAG-1" "AAACTCGCATTAGCCA-1" "AAACTCGGTTGCCGCA-1"
  [22] "AAACTCGTCGTGCTGG-1" "AAACTCGTCTGTAGAC-1" "AAACTGCAGCAATAAC-1"
  [25] "AAACTGCAGGATGTAT-1" "AAACTGCAGTACAGAT-1" "AAACTGCAGTCTCTAG-1"
  [28] "AAACTGCAGTGAAACT-1" "AAACTGCCAATTGGCT-1" "AAACTGCCACGTACAT-1"
  [31] "AAACTGCCATGACTGT-1" "AAACTGCGTACGGATG-1" "AAACTGCTCAGTGTGT-1"
  [34] "AAACTGCTCCATGACA-1" "AAACTGCTCCTCCCAA-1" "AAACTGCTCGAGTTAC-1"
  [37] "AAACTGCTCTCTCAAT-1" "AAAGATGAGAGGTGGG-1" "AAAGATGAGGAGTACC-1"
  [40] "AAAGATGCAACTCAAC-1" "AAAGATGCACTAGCCG-1" "AAAGATGCATGGGACA-1"
  [43] "AAAGATGCATTGCCTC-1" "AAAGATGGTGCGCTCA-1" "AAAGATGGTGTGCTTA-1"
  [46] "AAAGATGTCATGCTTT-1" "AAAGATGTCCTCCAGT-1" "AAAGATGTCCTGGAAT-1"
  [49] "AAAGATGTCTAAACGC-1" "AAAGATGTCTAGCAGT-1" "AAAGGATAGCGTTGCC-1"
  [52] "AAAGGATAGTCGACCC-1" "AAAGGATCAAAGGTCG-1" "AAAGGATCAAGCTTTG-1"
  [55] "AAAGGATCAATGGCTT-1" "AAAGGATCACAGCCAC-1" "AAAGGATCACGGCCAT-1"
  [58] "AAAGGATCATGTCCCT-1" "AAAGGATGTGATGTGG-1" "AAAGGATGTTGGCTAT-1"
  [61] "AAAGGATTCAAATGGA-1" "AAAGGATTCAACTTGG-1" "AAAGGATTCACACGTA-1"
  [64] "AAAGGATTCCAGAATC-1" "AAAGGGCAGCGTGTTT-1" "AAAGGGCAGGCCAGTA-1"
  [67] "AAAGGGCCACGATTAC-1" "AAAGGGCCATACAACC-1" "AAAGGGCCATTTAGGC-1"
  [70] "AAAGGGCGTAAGTGCG-1" "AAAGGGCGTTAGCTCA-1" "AAAGGGCGTTTAAGCC-1"
  [73] "AAAGGGCTCAACGTGT-1" "AAAGGGCTCACAGGGA-1" "AAAGGGCTCCGTGCGA-1"
  [76] "AAAGGGCTCGGATCGC-1" "AAAGGGCTCTTCCGTG-1" "AAATGAGAGAGACTCG-1"
  [79] "AAATGAGAGCTACGCC-1" "AAATGAGAGCTGATTC-1" "AAATGAGCAAAGGCCA-1"
  [82] "AAATGAGCAACGCAAG-1" "AAATGAGCAGGGTACA-1" "AAATGAGGTAACGGAC-1"
  [85] "AAATGAGGTAATGTAG-1" "AAATGAGGTATGGGTG-1" "AAATGAGTCCGCGATG-1"
  [88] "AAATGAGTCCGTGCAG-1" "AAATGAGTCGCACCGA-1" "AAATGAGTCTCTGCAC-1"
  [91] "AAATGAGTCTTCCACG-1" "AAATGAGTCTTGGCCT-1" "AAATGCCAGATGGCAC-1"
  [94] "AAATGCCAGCCGCAAA-1" "AAATGCCCACAGATGG-1" "AAATGCCCACATTCTT-1"
  [97] "AAATGCCGTAGTTTGC-1" "AAATGCCGTCAGCTTA-1" "AAATGCCGTGCATTCA-1"
 [100] "AAATGCCTCGTGGTAT-1" "AACAAAGAGACAGCTG-1" "AACAAAGAGACTCTTG-1"
 [103] "AACAAAGAGAGAGGTA-1" "AACAAAGAGCAGGAGG-1" "AACAAAGCAAGCAACG-1"
 [106] "AACAAAGCAGCAATGG-1" "AACAAAGCAGTCAGAG-1" "AACAAAGGTAAACGGC-1"
 [109] "AACAAAGGTAGTATCC-1" "AACAAAGGTGATTCCA-1" "AACAAAGGTGGAGTGT-1"
 [112] "AACAAAGGTTCTACCC-1" "AACAAAGGTTCTTTGT-1" "AACAAAGGTTGAATAG-1"
 [115] "AACAAAGTCACTCGGG-1" "AACAAAGTCAGCCGGT-1" "AACAAAGTCCAACCTC-1"
 [118] "AACAGTCAGCAGAGCT-1" "AACAGTCAGTCTTAGC-1" "AACAGTCCAACGTCGC-1"
 [121] "AACAGTCCACCGAAAG-1" "AACAGTCCACTTTGGA-1" "AACAGTCCATCCGTGG-1"
 [124] "AACAGTCCATCCTCGT-1" "AACAGTCCATGGCCCA-1" "AACAGTCCATTAGCAC-1"
 [127] "AACAGTCGTACCCATA-1" "AACAGTCGTAGAGAGA-1" "AACAGTCGTCAATACC-1"
 [130] "AACAGTCGTCTAAGAA-1" "AACAGTCTCAAACCCA-1" "AACATCGAGCTACGCC-1"
 [133] "AACATCGAGGAATGGA-1" "AACATCGAGGTTACAA-1" "AACATCGAGTACAACA-1"
 [136] "AACATCGAGTCTCGAT-1" "AACATCGCAGCAGGTA-1" "AACATCGCATTTGGTG-1"
 [139] "AACATCGGTTACTTTC-1" "AACATCGTCACAACAC-1" "AACATCGTCCTCTCTT-1"
 [142] "AACATCGTCGACTGGC-1" "AACCAACAGAAAGGGT-1" "AACCAACAGCGGACTA-1"
 [145] "AACCAACAGGATTTGA-1" "AACCAACAGGGAAGCG-1" "AACCAACAGTGTCCCG-1"
 [148] "AACCAACCAAAGGTCG-1" "AACCAACCACAAACAA-1" "AACCAACGTAAACGGC-1"
 [151] "AACCAACGTAGCATGG-1" "AACCAACGTCACAGGA-1" "AACCAACTCGCCACTT-1"
 [154] "AACCAACTCGGACGAA-1" "AACCAACTCTTCATAC-1" "AACCGATAGGGAAGCG-1"
 [157] "AACCGATCAATGACTC-1" "AACCGATCACCGAAAG-1" "AACCGATCATCCCTCA-1"
 [160] "AACCGATCATCTCTCG-1" "AACCGATCATTACCTT-1" "AACCGATTCGCATACA-1"
 [163] "AACCGATTCGTTCCGT-1" "AACCTGAAGAGCCTGA-1" "AACCTGAAGGCTGGAT-1"
 [166] "AACCTGAAGTGAGCAC-1" "AACCTGACAAGAAACT-1" "AACCTGACAAGAGATT-1"
 [169] "AACCTGACAGATTTGC-1" "AACCTGAGTAGACACG-1" "AACCTGAGTAGTGATA-1"
 [172] "AACCT

In [9]:
fragment_file <- file.path(cellr_indir, exp, "outs", "fragments.tsv.gz")
fragment_file
#fragment_indir <- file.path(cellr_indir, exp, "outs")

[1] "/data2/isshamie/mito_lineage/data/processed/mtscATAC/CHIP_april08_2021_Croker/MTblacklist/Flt3l/outs/fragments.tsv.gz"

## create a gene by cell FeatureMatrix

In [10]:
fragments <- CreateFragmentObject(fragment_file, cells, validate.fragments=TRUE)
fragments

Computing hash



A Fragment object for 5313 cells

In [11]:
gene.activities <- FeatureMatrix(
    fragments = fragments,
    features = genebodyandpromoter.coords,
    cells = cells,
    process_n = 32)
gene.activities

Extracting reads overlapping genomic regions

   [[ suppressing 32 column names 'AAACGAAAGGAAACTT-1', 'AAACGAAGTCCAAGAG-1', 'AAACGAAGTCCGAGCT-1' ... ]]

   [[ suppressing 32 column names 'AAACGAAAGGAAACTT-1', 'AAACGAAGTCCAAGAG-1', 'AAACGAAGTCCGAGCT-1' ... ]]

   [[ suppressing 32 column names 'AAACGAAAGGAAACTT-1', 'AAACGAAGTCCAAGAG-1', 'AAACGAAGTCCGAGCT-1' ... ]]



20314 x 5313 sparse Matrix of class "dgCMatrix"
                                                                                           
chr1-67091-70008         . . . . . . . . . . .  . . . . . . . . . . . .  . . . . . . . .  .
chr1-134901-141379       . . . . . . . . . . .  . . . . . . . . . . . .  . . . . . . . .  .
chr1-365640-368634       . . . . . . . . . . .  . . . . . . . . . . . .  . . . . . . . .  .
chr1-621059-624053       . . . . . . . . . . .  . . . . . . . . . . . .  . . . . . . . .  .
chr1-738532-741137       . . . . . . . . . . .  . . . . . . . . . . . .  . . . . . . . .  .
chr1-816043-819983       . . 2 . . 1 . . . . .  . . . . . . . . . . . .  . . . . . . . .  .
chr1-858260-879955       . . . . 1 . . . . . .  . . . . . . . . . 1 . 1  . . . . . . . .  .
chr1-861264-868445       . . . . 1 . . . . . .  . . . . . . . . . . . .  . . . . . . . .  .
chr1-879584-896689       . . . . 1 . . . . . .  . . . . . . . . . . . .  . . 1 . . . . .  .
chr1-893967-901095       . . . .

In [12]:
#     chunk = 10
#   )
# convert rownames from chromsomal coordinates into gene names
gene.key <- genebodyandpromoter.coords$gene_name
names(gene.key) <- GRangesToString(grange = genebodyandpromoter.coords)
rownames(gene.activities) <- gene.key[rownames(gene.activities)]
saveRDS(gene.activities, file =  paste0(outdir, exp,".gene_activities.rds"))



## Make ChromatinAssay

In [14]:
counts <- Read10X_h5(filename = file.path(singlecell_sumstats_dir, exp, "outs", "filtered_peak_bc_matrix.h5"))

metadata <- read.csv(
  file = file.path(singlecell_sumstats_dir, exp, "outs", "singlecell.csv"),
  header = TRUE,
  row.names = 1
)

counts

Warning message in sparseMatrix(i = indices[] + 1, p = indptr[], x = as.numeric(x = counts[]), :
"'giveCsparse' has been deprecated; setting 'repr = "T"' for you"
   [[ suppressing 31 column names 'AAACGAAAGGAAACTT-1', 'AAACGAAGTCCAAGAG-1', 'AAACGAAGTCCGAGCT-1' ... ]]

   [[ suppressing 31 column names 'AAACGAAAGGAAACTT-1', 'AAACGAAGTCCAAGAG-1', 'AAACGAAGTCCGAGCT-1' ... ]]

   [[ suppressing 31 column names 'AAACGAAAGGAAACTT-1', 'AAACGAAGTCCAAGAG-1', 'AAACGAAGTCCGAGCT-1' ... ]]



169455 x 5313 sparse Matrix of class "dgCMatrix"
                                                                                            
chr1:9872-10620        . . . . . . . . . . . . . . . . . . . . . . .  . . . . . . . . ......
chr1:96454-96767       . . . . . . . . . . . . . . . . . . . . . . .  . . . . . . . . ......
chr1:180692-181142     . . . . . . . . . . . . . . . . . . . . . . .  . . . . . . . . ......
chr1:191619-191976     . . . . . . . . . . . . . . . . . . . . . . .  . . . . . . . . ......
chr1:267770-268268     . . . . . . . . . . . . . . . . . . . . . . .  . . . . . . . . ......
chr1:271036-271547     . . . . . . . . . . . . . . . . . . . . . . 2  . . . . . . . . ......
chr1:274263-274577     . . . . . . . . . . . . . . . . . . . . . . .  . . . . . . . . ......
chr1:585946-586432     . . . . . . . . . . . . . . . . . . . . . . .  . . . . . . . . ......
chr1:605334-605817     . . . . . . . . . . . . . . . . . . . . . . .  . . . . . . . . ......
chr1:778276-779198   

In [15]:
rownames(counts)

[1] "chr1:9872-10620"           "chr1:96454-96767"         
    [3] "chr1:180692-181142"        "chr1:191619-191976"       
    [5] "chr1:267770-268268"        "chr1:271036-271547"       
    [7] "chr1:274263-274577"        "chr1:585946-586432"       
    [9] "chr1:605334-605817"        "chr1:778276-779198"       
   [11] "chr1:779814-779842"        "chr1:817102-817635"       
   [13] "chr1:825271-825373"        "chr1:826892-827922"       
   [15] "chr1:838278-838747"        "chr1:842781-843128"       
   [17] "chr1:869652-870208"        "chr1:890702-891078"       
   [19] "chr1:892280-892424"        "chr1:897322-897675"       
   [21] "chr1:898616-898800"        "chr1:904326-905680"       
   [23] "chr1:906604-907478"        "chr1:910607-911613"       
   [25] "chr1:912566-913253"        "chr1:916618-916983"       
   [27] "chr1:920622-921490"        "chr1:923174-924131"       
   [29] "chr1:924948-925854"        "chr1:936018-936020"       
   [31] "chr1:938061-938573"        "chr1:940140-942041"       
   [33] "chr1:955434-955865"        "chr1:958992-959646"       
   [35] "chr1:960302-961732"        "chr1:965864-967282"       
   [37] "chr1:968433-968641"        "chr1:969359-969832"       
   [39] "chr1:975939-976685"        "chr1:984095-984535"       
   [41] "chr1:997124-997507"        "chr1:998845-1001238"      
   [43] "chr1:1001761-1002252"      "chr1:1004869-1005628"     
   [45] "chr1:1013016-1014616"      "chr1:1015372-1015803"     
   [47] "chr1:1017501-1018222"      "chr1:1019026-1020267"     
   [49] "chr1:1021351-1021853"      "chr1:1022464-1023016"     
   [51] "chr1:1024137-1024521"      "chr1:1031964-1033511"     
   [53] "chr1:1034450-1034806"      "chr1:1035790-1036201"     
   [55] "chr1:1038619-1039981"      "chr1:1040522-1041151"     
   [57] "chr1:1042920-1043166"      "chr1:1058985-1059934"     
   [59] "chr1:1061866-1062216"      "chr1:1063729-1064666"     
   [61] "chr1:1065903-1065945"      "chr1:1066791-1067092"     
   [63] "chr1:1068427-1070268"      "chr1:1074766-1075129"     
   [65] "chr1:1079383-1080598"      "chr1:1091506-1092058"     
   [67] "chr1:1104086-1104658"      "chr1:1107428-1107614"     
   [69] "chr1:1109740-1110188"      "chr1:1112646-1112660"     
   [71] "chr1:1115708-1117908"      "chr1:1121890-1124667"     
   [73] "chr1:1125511-1125515"      "chr1:1135448-1135772"     
   [75] "chr1:1137302-1137774"      "chr1:1143989-1144724"     
   [77] "chr1:1157278-1158812"      "chr1:1166242-1166468"     
   [79] "chr1:1170133-1170314"      "chr1:1173584-1173836"     
   [81] "chr1:1177178-1177569"      "chr1:1182767-1183109"     
   [83] "chr1:1189047-1189521"      "chr1:1200891-1201901"     
   [85] "chr1:1205716-1206159"      "chr1:1207872-1209334"     
   [87] "chr1:1212709-1213869"      "chr1:1214553-1214995"     
   [89] "chr1:1230595-1232737"      "chr1:1241016-1241051"     
   [91] "chr1:1244420-1244560"      "chr1:1246438-1247251"     
   [93] "chr1:1250223-1250562"      "chr1:1251102-1251159"     
   [95] "chr1:1258595-1259028"      "chr1:1259955-1261564"     
   [97] "chr1:1262110-1262445"      "chr1:1264933-1265392"     
   [99] "chr1:1273106-1274618"      "chr1:1282034-1283333"     
  [101] "chr1:1284564-1284879"      "chr1:1290115-1290586"     
  [103] "chr1:1291739-1292248"      "chr1:1293687-1294207"     
  [105] "chr1:1299116-1299135"      "chr1:1300008-1300366"     
  [107] "chr1:1301958-1302352"      "chr1:1304525-1309870"     
  [109] "chr1:1324304-1325243"      "chr1:1331222-1331717"     
  [111] "chr1:1335266-1335268"      "chr1:1337760-1338058"     
  [113] "chr1:1344777-1345450"      "chr1:1348133-1350092"     
  [115] "chr1:1355307-1355838"      "chr1:1356693-1357162"     
  [117] "chr1:1358431-1359689"      "chr1:1360870-1361041"     
  [119] "chr1:1362073-1362369"      "chr1:1366766-1367631"     
  [121] "chr1:1371113-1372478"      "chr1:1374249-1376694"     
  [123] "chr1:1389743-1390097"      "chr1:1397828-1400715"     
  [125] "chr1:1401897-1402428"      

In [16]:
colnames(counts)

[1] "AAACGAAAGGAAACTT-1" "AAACGAAGTCCAAGAG-1" "AAACGAAGTCCGAGCT-1"
   [4] "AAACGAAGTTCAGAAA-1" "AAACGAAGTTTGAAGA-1" "AAACGAATCAGCCGGT-1"
   [7] "AAACGAATCCCAGTAA-1" "AAACGAATCCGGGCAT-1" "AAACGAATCCTGAAAC-1"
  [10] "AAACGAATCGATGTGT-1" "AAACGAATCGCCAGAC-1" "AAACGAATCGTGAACT-1"
  [13] "AAACTCGAGGAATGGA-1" "AAACTCGAGGTACACG-1" "AAACTCGCAAGACACG-1"
  [16] "AAACTCGCAATCCATG-1" "AAACTCGCACTAGGAG-1" "AAACTCGCACTGAAGG-1"
  [19] "AAACTCGCACTGTTAG-1" "AAACTCGCATTAGCCA-1" "AAACTCGGTTGCCGCA-1"
  [22] "AAACTCGTCGTGCTGG-1" "AAACTCGTCTGTAGAC-1" "AAACTGCAGCAATAAC-1"
  [25] "AAACTGCAGGATGTAT-1" "AAACTGCAGTACAGAT-1" "AAACTGCAGTCTCTAG-1"
  [28] "AAACTGCAGTGAAACT-1" "AAACTGCCAATTGGCT-1" "AAACTGCCACGTACAT-1"
  [31] "AAACTGCCATGACTGT-1" "AAACTGCGTACGGATG-1" "AAACTGCTCAGTGTGT-1"
  [34] "AAACTGCTCCATGACA-1" "AAACTGCTCCTCCCAA-1" "AAACTGCTCGAGTTAC-1"
  [37] "AAACTGCTCTCTCAAT-1" "AAAGATGAGAGGTGGG-1" "AAAGATGAGGAGTACC-1"
  [40] "AAAGATGCAACTCAAC-1" "AAAGATGCACTAGCCG-1" "AAAGATGCATGGGACA-1"
  [43] "AAAGATGCATTGCCTC-1" "AAAGATGGTGCGCTCA-1" "AAAGATGGTGTGCTTA-1"
  [46] "AAAGATGTCATGCTTT-1" "AAAGATGTCCTCCAGT-1" "AAAGATGTCCTGGAAT-1"
  [49] "AAAGATGTCTAAACGC-1" "AAAGATGTCTAGCAGT-1" "AAAGGATAGCGTTGCC-1"
  [52] "AAAGGATAGTCGACCC-1" "AAAGGATCAAAGGTCG-1" "AAAGGATCAAGCTTTG-1"
  [55] "AAAGGATCAATGGCTT-1" "AAAGGATCACAGCCAC-1" "AAAGGATCACGGCCAT-1"
  [58] "AAAGGATCATGTCCCT-1" "AAAGGATGTGATGTGG-1" "AAAGGATGTTGGCTAT-1"
  [61] "AAAGGATTCAAATGGA-1" "AAAGGATTCAACTTGG-1" "AAAGGATTCACACGTA-1"
  [64] "AAAGGATTCCAGAATC-1" "AAAGGGCAGCGTGTTT-1" "AAAGGGCAGGCCAGTA-1"
  [67] "AAAGGGCCACGATTAC-1" "AAAGGGCCATACAACC-1" "AAAGGGCCATTTAGGC-1"
  [70] "AAAGGGCGTAAGTGCG-1" "AAAGGGCGTTAGCTCA-1" "AAAGGGCGTTTAAGCC-1"
  [73] "AAAGGGCTCAACGTGT-1" "AAAGGGCTCACAGGGA-1" "AAAGGGCTCCGTGCGA-1"
  [76] "AAAGGGCTCGGATCGC-1" "AAAGGGCTCTTCCGTG-1" "AAATGAGAGAGACTCG-1"
  [79] "AAATGAGAGCTACGCC-1" "AAATGAGAGCTGATTC-1" "AAATGAGCAAAGGCCA-1"
  [82] "AAATGAGCAACGCAAG-1" "AAATGAGCAGGGTACA-1" "AAATGAGGTAACGGAC-1"
  [85] "AAATGAGGTAATGTAG-1" "AAATGAGGTATGGGTG-1" "AAATGAGTCCGCGATG-1"
  [88] "AAATGAGTCCGTGCAG-1" "AAATGAGTCGCACCGA-1" "AAATGAGTCTCTGCAC-1"
  [91] "AAATGAGTCTTCCACG-1" "AAATGAGTCTTGGCCT-1" "AAATGCCAGATGGCAC-1"
  [94] "AAATGCCAGCCGCAAA-1" "AAATGCCCACAGATGG-1" "AAATGCCCACATTCTT-1"
  [97] "AAATGCCGTAGTTTGC-1" "AAATGCCGTCAGCTTA-1" "AAATGCCGTGCATTCA-1"
 [100] "AAATGCCTCGTGGTAT-1" "AACAAAGAGACAGCTG-1" "AACAAAGAGACTCTTG-1"
 [103] "AACAAAGAGAGAGGTA-1" "AACAAAGAGCAGGAGG-1" "AACAAAGCAAGCAACG-1"
 [106] "AACAAAGCAGCAATGG-1" "AACAAAGCAGTCAGAG-1" "AACAAAGGTAAACGGC-1"
 [109] "AACAAAGGTAGTATCC-1" "AACAAAGGTGATTCCA-1" "AACAAAGGTGGAGTGT-1"
 [112] "AACAAAGGTTCTACCC-1" "AACAAAGGTTCTTTGT-1" "AACAAAGGTTGAATAG-1"
 [115] "AACAAAGTCACTCGGG-1" "AACAAAGTCAGCCGGT-1" "AACAAAGTCCAACCTC-1"
 [118] "AACAGTCAGCAGAGCT-1" "AACAGTCAGTCTTAGC-1" "AACAGTCCAACGTCGC-1"
 [121] "AACAGTCCACCGAAAG-1" "AACAGTCCACTTTGGA-1" "AACAGTCCATCCGTGG-1"
 [124] "AACAGTCCATCCTCGT-1" "AACAGTCCATGGCCCA-1" "AACAGTCCATTAGCAC-1"
 [127] "AACAGTCGTACCCATA-1" "AACAGTCGTAGAGAGA-1" "AACAGTCGTCAATACC-1"
 [130] "AACAGTCGTCTAAGAA-1" "AACAGTCTCAAACCCA-1" "AACATCGAGCTACGCC-1"
 [133] "AACATCGAGGAATGGA-1" "AACATCGAGGTTACAA-1" "AACATCGAGTACAACA-1"
 [136] "AACATCGAGTCTCGAT-1" "AACATCGCAGCAGGTA-1" "AACATCGCATTTGGTG-1"
 [139] "AACATCGGTTACTTTC-1" "AACATCGTCACAACAC-1" "AACATCGTCCTCTCTT-1"
 [142] "AACATCGTCGACTGGC-1" "AACCAACAGAAAGGGT-1" "AACCAACAGCGGACTA-1"
 [145] "AACCAACAGGATTTGA-1" "AACCAACAGGGAAGCG-1" "AACCAACAGTGTCCCG-1"
 [148] "AACCAACCAAAGGTCG-1" "AACCAACCACAAACAA-1" "AACCAACGTAAACGGC-1"
 [151] "AACCAACGTAGCATGG-1" "AACCAACGTCACAGGA-1" "AACCAACTCGCCACTT-1"
 [154] "AACCAACTCGGACGAA-1" "AACCAACTCTTCATAC-1" "AACCGATAGGGAAGCG-1"
 [157] "AACCGATCAATGACTC-1" "AACCGATCACCGAAAG-1" "AACCGATCATCCCTCA-1"
 [160] "AACCGATCATCTCTCG-1" "AACCGATCATTACCTT-1" "AACCGATTCGCATACA-1"
 [163] "AACCGATTCGTTCCGT-1" "AACCTGAAGAGCCTGA-1" "AACCTGAAGGCTGGAT-1"
 [166] "AACCTGAAGTGAGCAC-1" "AACCTGACAAGAAACT-1" "AACCTGACAAGAGATT-1"
 [169] "AACCTGACAGATTTGC-1" "AACCTGAGTAGACACG-1" "AACCTGAGTAGTGATA-1"
 [172] "AACCT

In [17]:
chrom_assay <- CreateChromatinAssay(
  counts = counts,
  sep = c(":", "-"),
  genome = 'hg38',
  fragments = fragment_file,
  min.cells = 10,
  min.features = 200
)

cd34 <- CreateSeuratObject(
  counts = chrom_assay,
  assay = "peaks",
  meta.data = metadata
)

Computing hash

Warning message in CreateSeuratObject.Assay(counts = chrom_assay, assay = "peaks", :
"Some cells in meta.data not present in provided counts matrix."


In [18]:
cd34

An object of class Seurat 
160368 features across 5312 samples within 1 assay 
Active assay: peaks (160368 features, 0 variable features)

In [19]:
# extract gene annotations from EnsDb
annotations <- GetGRangesFromEnsDb(ensdb = EnsDb.Hsapiens.v75, biotypes = "protein_coding")
seqlevelsStyle(annotations) <- 'UCSC'
genome(annotations) <- "hg38"

Fetching data...
OK

Parsing exons...
OK
Defining introns...
OK
Defining UTRs...
OK
Defining CDS...
OK

aggregating...

Done

Fetching data...
OK

Parsing exons...
OK
Defining introns...
OK
Defining UTRs...
OK
Defining CDS...
OK

aggregating...

Done

Fetching data...
OK

Parsing exons...
OK
Defining introns...
OK
Defining UTRs...
OK
Defining CDS...
OK

aggregating...

Done

Fetching data...
OK

Parsing exons...
OK
Defining introns...
OK
Defining UTRs...
OK
Defining CDS...
OK

aggregating...

Done

Fetching data...
OK

Parsing exons...
OK
Defining introns...
OK
Defining UTRs...
OK
Defining CDS...
OK

aggregating...

Done

Fetching data...
OK

Parsing exons...
OK
Defining introns...
OK
Defining UTRs...
OK
Defining CDS...
OK

aggregating...

Done

Fetching data...
OK

Parsing exons...
OK
Defining introns...
OK
Defining UTRs...
OK
Defining CDS...
OK

aggregating...

Done

Fetching data...
OK

Parsing exons...
OK
Defining introns...
OK
Defining UTRs...
OK
Defining CDS...
OK

aggregating...

In [32]:
annotations

GRanges object with 2996573 ranges and 5 metadata columns:
                  seqnames        ranges strand |           tx_id   gene_name
                     <Rle>     <IRanges>  <Rle> |     <character> <character>
  ENSE00001489430     chrX 192989-193061      + | ENST00000399012      PLCXD1
  ENSE00001536003     chrX 192991-193061      + | ENST00000484611      PLCXD1
  ENSE00002160563     chrX 193020-193061      + | ENST00000430923      PLCXD1
  ENSE00001750899     chrX 197722-197788      + | ENST00000445062      PLCXD1
  ENSE00001489388     chrX 197859-198351      + | ENST00000381657      PLCXD1
              ...      ...           ...    ... .             ...         ...
  ENST00000361739    chrMT     7586-8269      + | ENST00000361739      MT-CO2
  ENST00000361789    chrMT   14747-15887      + | ENST00000361789      MT-CYB
  ENST00000361851    chrMT     8366-8572      + | ENST00000361851     MT-ATP8
  ENST00000361899    chrMT     8527-9207      + | ENST00000361899     MT-ATP6
  ENS

In [20]:
# add the gene information to the object
Annotation(cd34) <- annotations

In [ ]:
# change to UCSC style since the data was mapped to hg19
gene.activities <- GeneActivity(cd34)

In [ ]:

# add the gene activity matrix to the Seurat object as a new assay and normalize it
cd34[['RNA']] <- CreateAssayObject(counts = gene.activities)
cd34 <- NormalizeData(
  object = cd34,
  assay = 'RNA',
  normalization.method = 'LogNormalize',
  scale.factor = median(cd34$nCount_RNA)
)

In [ ]:
assays(cd34)

## Analysis if wanted

In [ ]:
cd34 <- RunTFIDF(cd34)
cd34 <- FindTopFeatures(cd34, min.cutoff = 'q0')
cd34 <- RunSVD(cd34)

In [ ]:
cd34 <- RunUMAP(object = cd34, reduction = 'lsi', dims = 2:30)
cd34 <- FindNeighbors(object = cd34, reduction = 'lsi', dims = 2:30)
cd34 <- FindClusters(object = cd34, verbose = FALSE, algorithm = 3)
DimPlot(object = cd34, label = TRUE) + NoLegend()

In [ ]:
DefaultAssay(cd34) <- 'RNA'

FeaturePlot(
  object = cd34,
  features = c('MS4A1', 'CD3D', 'LEF1', 'NKG7', 'TREM1', 'LYZ'),
  pt.size = 0.1,
  max.cutoff = 'q95',
  ncol = 3
)

## Subset on overlapping genes

In [ ]:
sessionInfo()